In [ ]:
import xgt
# Connect to server
server = xgt.Connection()

# Drop all objects
[server.drop_frame(f) for f in ['ReportsTo', 'Employees']]

# Define and create the graph schema in the "demo" namespace
employees = server.create_vertex_frame(
  name='Employees',
  schema=[['person_id', xgt.INT],
          ['name', xgt.TEXT],
          ['postal_code', xgt.INT]],
  key='person_id')

reports_to = server.create_edge_frame(
  name='ReportsTo',
  schema=[['employee_id', xgt.INT],
          ['boss_id', xgt.INT],
          ['start_date', xgt.DATE],
          ['end_date', xgt.DATE]],
  source=employees,
  target=employees,
  source_key='employee_id',
  target_key='boss_id')

# Load data to the graph in the xGT server.
# Use the insert() method for data of a few hundred rows or fewer;
# for bigger amounts of data, use the load() method with CSV files.
employees.insert(
  [[111111101, 'Manny', 98103],
   [111111102, 'Trish', 98108],
   [911111501, 'Frank', 98101],
   [911111502, 'Alice', 98102]
  ])
reports_to.insert(
  [[111111101, 911111501, '2015-01-03', '2017-04-14'],
   [111111102, 911111501, '2016-04-02', '2017-04-14'],
   [911111502, 911111501, '2016-07-07', '2017-04-14'],
   [111111101, 911111502, '2017-04-15', None],
   [111111102, 911111502, '2017-04-15', None],
   [911111501, 911111502, '2017-04-15', None]
  ])

In [ ]:
def run_query(server, query):
    j=server.run_job(query)
    return j.get_data_pandas()

In [ ]:
# Example Query
run_query(server, """
  MATCH (employee:Employees)-[edge1:ReportsTo]->
        (boss:Employees)-[edge2:ReportsTo]->(employee)
  WHERE
    edge1.end_date <= edge2.start_date
  RETURN
    employee.person_id AS employee1_id,
    boss.person_id AS employee2_id,
    edge1.start_date AS start1,
    edge1.end_date AS end1,
    edge2.start_date AS start2,
    edge2.end_date AS end2
""")

In [ ]:
# Cleanup, drop all objects
[server.drop_frame(f) for f in [reports_to, employees]]